In [2]:
# coding: utf-8
import pygentoolbox
import time
import os

import numpy as np
from numpy.polynomial import polynomial
import pandas as pd

import matplotlib.pyplot as plt
import datashader as ds
import datashader.transfer_functions as tf
print('done')

done


In [3]:
plt.style.use("seaborn-whitegrid")

# Each column is was one data sample
# i reformatted the data to two colums
# first column is number from 0 - 5 representing timecourse timepoints, 0=VEG,1=MEI,2=FRG,3=DEV1,4=DEV2/3,5=DEV4
# second column is the gene expression values from ParameciumDB for genes overlapping SRCs
filepath = 'D:\\LinuxShare\\Projects\\Theresa\\SRCs\\SRCs.NoPtiwi08.dataframe.1ColPerGene.tsv'
path, f = os.path.split(filepath)
df = pd.read_csv(filepath, sep='\t')

#divide each column by max value from that column
#df = np.log2(df)
df = df / df.max()
df = np.round(df, decimals=2)
print(df.isin([1.00]).sum(axis=1))  # count number of times 1.00 (the max value) is present in each timepoint

df.head(n=6)


#df = np.log2(df)
#df = np.round(df, decimals=2)
#df.head(n=6)

#### add column log2(gene expression)
###df['geneexpr_log2'] = np.log2(df['geneexpr'])
###delete old geneexpr column
###df.drop('geneexpr', inplace=True, axis=1)
###df.head()

0    805
1    223
2    148
3    170
4    355
5    634
dtype: int64


1     2     3     4     5     6     7     8     9    10  ...  2285  \
0  0.58  0.58  0.88  1.00  0.74  0.32  0.53  1.00  0.51  0.47  ...  1.00   
1  0.75  0.75  1.00  0.72  0.40  1.00  0.40  0.67  0.41  0.47  ...  0.39   
2  0.64  0.64  0.30  0.40  0.53  0.84  0.41  0.44  0.43  0.49  ...  0.11   
3  0.59  0.59  0.21  0.35  0.89  0.80  0.82  0.45  0.51  0.63  ...  0.19   
4  1.00  1.00  0.67  0.53  0.95  0.93  0.91  0.46  0.70  0.93  ...  0.58   
5  0.92  0.92  0.41  0.44  1.00  0.78  1.00  0.46  1.00  1.00  ...  0.29   

   2286  2287  2288  2289  2290  2291  2292  2293  2294  
0  0.73  0.53  1.00  0.81  0.36  1.00  0.08  0.08  0.08  
1  0.47  0.81  0.44  0.62  0.61  0.82  0.58  0.58  0.58  
2  0.36  0.98  0.39  0.91  0.75  0.52  0.34  0.34  0.34  
3  0.48  0.99  0.29  0.76  0.92  0.49  0.71  0.71  0.71  
4  0.44  0.84  0.41  0.86  0.97  0.38  0.95  0.95  0.95  
5  1.00  1.00  0.49  1.00  1.00  0.50  1.00  1.00  1.00  

[6 rows x 2294 columns]

In [4]:

# Append row with nan-values
df = df.append(pd.DataFrame([np.array([np.nan] * len(df.columns))], columns=df.columns, index=[np.nan]))

# Reshape
x, y = df.shape
arr = df.values.reshape((x * y, 1), order='F')
df_reshaped = pd.DataFrame(arr, columns=list('y'), index=np.tile(df.index.values, y))
df_reshaped = df_reshaped.reset_index()
df_reshaped.columns.values[0] = 'x'
print(df_reshaped.head(n=7))


# Plotting parameters
x_range = (min(df.index.values), max(df.index.values))
y_range = (df.min().min(), df.max().max())
w = 1000
h = 750
dpi = 150
dpiscaling = 25  # use 5 or something, not really required
cvs = ds.Canvas(x_range=x_range, y_range=y_range, plot_height=h, plot_width=w)

# Aggregate data
t0 = time.time()
aggs = cvs.line(df_reshaped, 'x', 'y', ds.count())
print("Time to aggregate line data: {}".format(time.time()-t0))

# One colored plot
t1 = time.time()
stacked_img = tf.Image(tf.shade(aggs, cmap=["darkblue", "darkblue"]))
print("Time to create stacked image: {}".format(time.time() - t1))

# Save
f0 = plt.figure(figsize=(w / dpi, h / dpi), dpi=dpi*dpiscaling)
ax0 = f0.add_subplot(111)
ax0.imshow(stacked_img.to_pil())
ax0.grid(False)
outfile = os.path.join(path, "stacked.png")
f0.savefig(outfile, bbox_inches="tight", dpi=dpi*dpiscaling)

# Heat map - This uses a equalized histogram (built-in default), there are other options, though.
t2 = time.time()
heatmap_img = tf.Image(tf.shade(aggs, cmap=plt.cm.Spectral_r))
print("Time to create stacked image: {}".format(time.time() - t2))

# Save
f1 = plt.figure(figsize=(w / dpi, h / dpi), dpi=dpi*dpiscaling)
ax1 = f1.add_subplot(111)
ax1.imshow(heatmap_img.to_pil())
ax1.grid(False)
outfile = os.path.join(path, "heatmap.png")
f1.savefig(outfile, bbox_inches="tight", dpi=dpi*dpiscaling)

     x     y
0  0.0  0.58
1  1.0  0.75
2  2.0  0.64
3  3.0  0.59
4  4.0  1.00
5  5.0  0.92
6  NaN   NaN
Time to aggregate line data: 2.076932907104492
Time to create stacked image: 0.08179616928100586
Time to create stacked image: 0.07077789306640625


In [3]:


# coding: utf-8
import pygentoolbox
import time

import numpy as np
from numpy.polynomial import polynomial
import pandas as pd

import matplotlib.pyplot as plt
import datashader as ds
import datashader.transfer_functions as tf

plt.style.use("seaborn-whitegrid")

def create_data():
    # ...

# Each column is one data sample
df = create_data()

# Following will append a nan-row and reshape the dataframe into two columns, with each sample stacked on top of each other
#   THIS IS CRUCIAL TO OPTIMIZE SPEED: https://github.com/bokeh/datashader/issues/286

# Append row with nan-values
df = df.append(pd.DataFrame([np.array([np.nan] * len(df.columns))], columns=df.columns, index=[np.nan]))

# Reshape
x, y = df.shape
arr = df.as_matrix().reshape((x * y, 1), order='F')
df_reshaped = pd.DataFrame(arr, columns=list('y'), index=np.tile(df.index.values, y))
df_reshaped = df_reshaped.reset_index()
df_reshaped.columns.values[0] = 'x'

# Plotting parameters
x_range = (min(df.index.values), max(df.index.values))
y_range = (df.min().min(), df.max().max())
w = 1000
h = 750
dpi = 150
cvs = ds.Canvas(x_range=x_range, y_range=y_range, plot_height=h, plot_width=w)

# Aggregate data
t0 = time.time()
aggs = cvs.line(df_reshaped, 'x', 'y', ds.count())
print("Time to aggregate line data: {}".format(time.time()-t0))

# One colored plot
t1 = time.time()
stacked_img = tf.Image(tf.shade(aggs, cmap=["darkblue", "darkblue"]))
print("Time to create stacked image: {}".format(time.time() - t1))

# Save
f0 = plt.figure(figsize=(w / dpi, h / dpi), dpi=dpi)
ax0 = f0.add_subplot(111)
ax0.imshow(stacked_img.to_pil())
ax0.grid(False)
f0.savefig("stacked.png", bbox_inches="tight", dpi=dpi)

# Heat map - This uses a equalized histogram (built-in default), there are other options, though.
t2 = time.time()
heatmap_img = tf.Image(tf.shade(aggs, cmap=plt.cm.Spectral_r))
print("Time to create stacked image: {}".format(time.time() - t2))

# Save
f1 = plt.figure(figsize=(w / dpi, h / dpi), dpi=dpi)
ax1 = f1.add_subplot(111)
ax1.imshow(heatmap_img.to_pil())
ax1.grid(False)
f1.savefig("heatmap.png", bbox_inches="tight", dpi=dpi)

IndentationError: expected an indented block (<ipython-input-3-aa8a30b0bd87>, line 7)